In [7]:
import pandas as pd
from bertopic import BERTopic
from sklearn.feature_extraction.text import CountVectorizer

In [8]:
# Load csv files, that were cleaned and transformed using the 2_clean_transform notebook

bg_df = pd.read_csv("./data/bulgarian_submissions.csv", index_col=0)
bg_df['created_utc'] = pd.to_datetime(bg_df.created_utc)
bg_df['created_utc'] = bg_df['created_utc'].dt.date
bg_df['created_utc']=bg_df['created_utc'].astype(str)

bg_comments = pd.read_csv("./data/bulgarian_comments.csv", index_col=0)
bg_comments['body'] = bg_comments['body'].str.lower()

/var/folders/w8/bk8xzzt10l30g9c3zpfjjh700000gn/T/ipykernel_65861/504221634.py:8: DtypeWarning: Columns (9) have mixed types. Specify dtype option on import or set low_memory=False.
  bg_comments = pd.read_csv("./data/bulgarian_comments.csv", index_col=0)


In [9]:
# Get documents and timestamps for BERTopic
texts = bg_df['body'].values.tolist()
timestamps = bg_df['created_utc'].values.tolist()

In [10]:
# Load stopwords
# Using list comprehension
with open('custom_stopwords.txt', 'r') as file:
    stopwords = [line.strip() for line in file]

# Let's get a list of stopwords in bulgarian
bg_stopwords = set(stopwords)
bg_stopwords = list(bg_stopwords)

In [25]:
# Let's make the first BERTopic model (after some experimentation with the parameters I decided to add mind_df=10, which would exclude all
# words that have frequency less than 10 in the corpus)
vectorizer_model = CountVectorizer(stop_words=bg_stopwords, min_df=10)
topic_model = BERTopic(verbose=True, embedding_model="paraphrase-multilingual-mpnet-base-v2", vectorizer_model=vectorizer_model, min_topic_size=50, calculate_probabilities=True)
topics, probs = topic_model.fit_transform(texts)

2024-04-16 11:09:33,275 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/1678 [00:00<?, ?it/s]

2024-04-16 11:19:37,226 - BERTopic - Embedding - Completed ✓
2024-04-16 11:19:37,227 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-04-16 11:19:56,283 - BERTopic - Dimensionality - Completed ✓
2024-04-16 11:19:56,285 - BERTopic - Cluster - Start clustering the reduced embeddings


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

2024-04-16 11:20:30,259 - BERTopic - Cluster - Completed ✓
2024-04-16 11:20:30,266 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-04-16 11:20:30,696 - BERTopic - Representation - Completed ✓


In [34]:
# Reduce outliers using probabilities
new_topics = topic_model.reduce_outliers(texts, topics , probabilities=probs, strategy="probabilities", threshold=0.05)
# Reduce outliers using the `distributions` strategy
topic_model.update_topics(texts, topics=new_topics)

2024-04-16 11:29:30,008 - BERTopic - WARNING: Using a custom list of topic assignments may lead to errors if topic reduction techniques are used afterwards. Make sure that manually assigning topics is the last step in the pipeline.Note that topic embeddings will also be created through weightedc-TF-IDF embeddings instead of centroid embeddings.


In [ ]:
# We could save the model to disk and load it instead of having to train it again
# embedding_model = "sentence-transformers/paraphrase-multilingual-mpnet-base-v2"
# topic_model.save("path/to/my/model_dir", serialization="pytorch", save_ctfidf=True, save_embedding_model=embedding_model)

In [40]:
heatmap = topic_model.visualize_heatmap( title="")
heatmap

In [28]:
hierarchical_topics = topic_model.hierarchical_topics(texts)
hierarchical= topic_model.visualize_hierarchy(hierarchical_topics=hierarchical_topics,  title="")
hierarchical

100%|██████████| 147/147 [00:00<00:00, 282.58it/s]


In [36]:
## Merging topics. After manually inspecting each topic and using the hierarchical visualization with the heatmap I have 
# found some topics, that could be merged to improve the topic representation 
topics_to_merge = [[134, 9],
                   [118, 8], 
                   [59,130],
                   [93,21],
                   [74,14,41,139],
                   [87,18],
                   [3,122],
                   [53,13],
                   [50,126],
                   [24,96],
                   [4,6],
                   [82,75,23],
                   [143,91],
                   [19,73],
                   [35,34],
                   [56,81],
                   [62,133,106,46,66,55],
                   [99,142],
                   [33,45],
                   [39,68],
                   [69,7],
                   [108,27],
                   [37,67],
                   [10,25],
                   [95,72],
                   [138,22],
                   [43,129], 
                   [141,146,29,140],
                   [70,40],
                   [71,48],
                   [31,36]]


topic_model.merge_topics(texts, topics_to_merge)

In [41]:
# Now since I didn't use the random_state parameter to prevent stochastic behavior, even if you repeat the steps 
# the end result won'be the same (https://maartengr.github.io/BERTopic/getting_started/best_practices/best_practices.html#preventing-stochastic-behavior)
# So instead of that let's load the model. First download it from huggingface (link in readme) and then just load the whole directory

# Load from directory
topic_model = BERTopic.load("./bg_reddit_model")

In [42]:
topic_model.visualize_heatmap()

In [43]:
# After that let's give those topics better names. While I was selecting which topics to merge, I also took notes on what is each topic about
# and I used those notes to create better labels (albeit quite long)

new_labels = {0: "Други обсъждания (не са свързани с конкретна категория по-скоро е internet chatter)", 
1:"Вътрешна политика(основно обсъждания около партии и личности)", 
2:"Конспиративни теории и езотерика",
3:"Животът в България - всякакви обсъждания",
4:"Конспиративни теории, клюки и други нискокачествени постове (с малко false positive като например статии от mediapool и др.)",
5:"Войната между Украйна и Русия",
6:"Описания на снимки от България",
7:"Вътрешна политика и публична администрация (обсъждания около съда, законодателството, МВР)",
8:"Въпроси тип лексикон",
9:"ЕС, НАТО и мястото на България в света(Външна политика)",
10:"Българска история и национализъм",
11:"Основно София и някои други градове в България (почивка, битови въпроси, градски дискусии)",
12:"Междугрупови сравнения и въпроси (напр. “българите сме”, “защо мразим чужденците”… )",
13:"Автомобили и пътна обстановка",
14:"Ковид, маски и ваксини",
15:"Храни и рецепти",
16:"Празници, исторически дати и обсъждания около тях",
17:"Политика и правителство (особено обсъждания около съставянето на правителство)",
18:"Бюрокрация свързана с финанси (електронни подписи, лични финанси, бизнес, митници)",
19:"Нискокачествени смесени постове (всякакви теми)",
20:"Клюки, видеа и други",
21:"Интериорни врати (нещо като реклама)",
22:"Заплати, доходи и пенсии",
23:"Северна Македония и македонската култура във връзка с България",
24:"Български език и други езици, както и дискусии около азбуки",
25:"Филми и телевизия (различни обсъждания на шоута, сайтове, кина и др.)",
26:"Финанси на българите",
27:"Протести и други прояви на неконформизъм (напр. Луков марш)",
28:"Изборите в България",
29:"Домакинство и електроуреди/инструменти",
30:"Образование - формално и неформално",
31:"Здравеопазване и въпроси свързани с болести (но без Ковид)",
32:"Журналистика, новини и медии (с някои outliers )",
33:"Други дискусии около избори и гласуване (референдуми, трябва ли да гласуваме и др.)",
34:"Oбсъждания за времето(за части от деня и седмицата). Основно outliers.",
35:"Вътрешна и външна сигурност (войни, престъпления, криминални лица)",
36:"Политиката в България - основно обсъждания около политическите идеологии, а не обсъждания на партии и личности",
37:"Интернет, мобилни мрежи и телефони",
38:"Криминални новини и престъпления",
39:"Семейство, секс и деца",
40:"Mемета",
41:"Музика (обсъждания около песни, сайтове, права)",
42:"Имоти и наеми",
43:"Животни и домашни любимци",
44:"Футбол, Евровизия, Игри на волята и други събития със състезателен или спортен характер",
45:"Обсъждания около книги",
46:"Газови доставки и търговията на зърно по време на войната между Украйна и Русия",
47:"Физически магазини и шопинг (основно дрехи)",
48:"Политика и идеологически спорове и дискусии",
49:"Oбсъждания около знамена (не само българското) и флагове. Много обсъждания свързани с българското знаме в събредита /r/place/",
50:"Описания на снимки основно от София",
51:"Дискусии около време и промяна",
52:"Самолети, дронове, хеликоптери",
53:"Транспорт - междуградски и градски",
54:"Онлайн Пазаруване",
55:"Компютри & Периферия (вкл. 3D принтиране и гейминг)",
56:"Комунизъм и фашизъм (основно във връзка с България)",
57:"Демографски обсъждания свързани с България",
58:"Клипове и видеа в интернет",
59:"Какво мислите за…? (някои обсъждания са политически, но като цяло е смесица от всичко)",
60:"Нискокачествени исторически публикации",
61:"Запознанства - сайтове и дискусии",
62:"Смесени емоционално заредени постове (много ! или All Caps)",
63:"Интернет шеги и мемета",
64:"Проучвания, анкети и тестове",
65:"Пътувания и местения в чужбина -  административни и други дискусии",
66:"Почивка и туризъм на море (основно Черно море)",
67:"Икономика (основно обсъждания за българската икономика)",
68:"Изкуствен интелект и наука",
69:"Балканите (основно Сърбия) - обсъждания около исторически събития и политика",
70:"Влакове (#trainspotting)",
71:"ЛГБТ и полова ориентация",
72:"Алкохол и други напитки",
73:"Видео игри",
74:"Какво избирате? (сравнение и въпроси за всякакви теми)",
75:"Обсъждания на пропаганда и лъжи (основно политически)",
76:"Културни паметници и църкви",
77:"Археология",
78:"Пътувания и почивки",
79:"Цените на ток, вода, тец и стоки",
80:"Зима и температури",
81:"Турция и Гърция (Външна политика)",
82:"Социалните мрежи и Фейсбук",
83:"Партия Възраждане, Апокалипсиса и зловещи преживявания (странна комбинация, може би заради мистичното значение на думата възраждане извън контекста на политическа партия или исторически период)",
84:"Фитнес, упражнения и здравословен начин на живот",
85:"Интернет, спам и киберсигурност",
86:"Неполитически новини и любопитни факти от света и България (стил списание)",
87:"Политика и корупция",
88:"Българска музика",
89:"Пушене (цигари/марихуана)",
90:"Паметник на съветската армия и други паметници",
91:"Приятелство, връзки и съвети около казуси от социалния живот",
92:"Козметика и грижа за външния вид",
93:"Кафета и ресторанти - препоръки и дискусии",
94:"Очи и сън (странна комбинация, вероятно комбинация от outliers)",
95:"Инвестиции (основно акции и etf-и)",
96:"Криптовалути",
97:"Аудио книги",
98:"Забавни реклами или обсъждания на рекламни клипове",
99:"Шеги и иронични постове свързани с Бойко Борисов и други публични личности",
100:"Постове с ниско качество (основно outliers, някои криминални)",
101:"Котки",
102:"Хазарт",
103:"Стипендии, семинари и обсъждания за финансиране на проекти",
104:"Данъци",
105:"Зелен сертификат",
106:"Демокрация и политика",
107:"Психология и терапия",
108:"Кисело мляко",
109:"Обсъждания основно свързани с /r/place/",
110:"Отопление - технологии и проблеми",
111:"Инфлацията в България и света",
112:"Демографска криза и преброяване",
}

In [44]:
# Function to Wrap labels
def wrap_labels_dict(labels_dict, char_limit=35):
    """Wrap the text in dictionary values by inserting line breaks."""
    wrapped_labels_dict = {}
    for key, label in labels_dict.items():
        wrapped_label = ''
        current_line_length = 0
        for word in label.split(' '):
            if current_line_length + len(word) + 1 > char_limit:
                wrapped_label += '<br>' + word
                current_line_length = len(word)
            else:
                if wrapped_label != '':  # Add space if not at the beginning
                    wrapped_label += ' '
                    current_line_length += 1
                wrapped_label += word
                current_line_length += len(word)
        wrapped_labels_dict[key] = wrapped_label
    return wrapped_labels_dict

In [45]:
# Wrap the labels in the dictionary
wrapped_labels_dict = wrap_labels_dict(new_labels, 40)


# After that we can add the new names 
topic_model.set_topic_labels(wrapped_labels_dict)

In [57]:
df_topics = topic_model.get_topic_info()
len(df_topics)

113

In [58]:
df_topics["Proportion"] = df_topics['Count'] / (df_topics['Count'].sum())
df_topics["Proportion"] = df_topics["Proportion"].round(3)

In [62]:
import plotly.express as px
fig = px.bar(df_topics.head(15), x="Proportion", y="CustomName", orientation='h', color='CustomName', text="Proportion", template="plotly_white", title="Топ 15 теми в /r/bulgaria", color_discrete_sequence=px.colors.qualitative.Vivid)
fig.update_layout(xaxis_title="Пропорция", yaxis_title="", showlegend=False, height=800)
fig.update_yaxes(categoryorder='total ascending')
fig.show()

In [71]:
# Get lists of topics for each category to later merge into the main Topic model
pol_category = pd.read_csv("topics_categories.csv")
pol_category = pol_category.rename(columns={"Unnamed: 0" : "Topic"})

In [72]:
df_topics = df_topics.merge(pol_category, on="Topic")
merging_categories_topics = df_topics.groupby("Category")['Topic'].apply(list).reset_index()
df_combined = df_topics.groupby("Category").sum().reset_index()
df_combined["Proportion"] = df_combined["Proportion"].round(3)

In [73]:
import plotly.express as px
fig = px.bar(df_combined, x="Proportion", y="Category", orientation='h', color='Category', text="Proportion", template="plotly_white", title="", color_discrete_sequence=px.colors.qualitative.Vivid)
fig.update_layout(xaxis_title="Пропорция", yaxis_title="", showlegend=False, height=600,  autosize=False, width=1000, margin=dict(l=20, r=20
, t=0, b=20)) 
fig.update_yaxes(categoryorder='total ascending')
fig.show()

In [75]:
topics_over_time = topic_model.topics_over_time(texts, timestamps, nr_bins=60)

60it [00:17,  3.43it/s]


In [76]:
time = topic_model.visualize_topics_over_time(topics_over_time, topics=[5, 8, 14, 15], custom_labels=True, title="")
time

In [77]:
documents_fig = topic_model.visualize_documents(texts, hide_document_hover=False, hide_annotations=True, custom_labels=True, title="")
documents_fig